In [1]:
import pandas as pd
import numpy as np
import os
import latextable
from texttable import Texttable
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import pprint
import scipy.stats
import itertools
import plotly.express as px
import wandb

In [2]:
def load_dataset(path):
    dataset = pd.read_csv(path)
    dataset['close_time'] = pd.to_datetime(dataset['close_time'])
    dataset['open_time'] = pd.to_datetime(dataset['open_time'])
    return dataset

In [3]:
btc_usdt_5_min_data = load_dataset('../data/preprocessed_data/processed-btc-usdt-5m.csv')
btc_usdt_15_min_data = load_dataset('../data/preprocessed_data/processed-btc-usdt-15m.csv')
btc_usdt_30_min_data = load_dataset('../data/preprocessed_data/processed-btc-usdt-30m.csv')

In [4]:
NUM_WINDOWS=6
LIMIT_TIME = pd.Timestamp(year=2024, month=7, day=25, hour=23, minute=59)

def trim_number_of_observations(data, limit_time):
    return data.loc[data['close_time'] <= limit_time]

def get_trimmed_data(
        data, 
        num_parts,
        limit_time,
        in_sample_size,
        out_of_sample_size):

    data = trim_number_of_observations(data, limit_time=limit_time)
    data = data.iloc[-(in_sample_size + (num_parts * out_of_sample_size)):]
    return data

In [5]:
btc_usdt_5_min_data = get_trimmed_data(
    btc_usdt_5_min_data,
    NUM_WINDOWS,
    LIMIT_TIME,
    in_sample_size=(24 * 30 * 24 * (60 // 5)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 5)) # 6 months
)
btc_usdt_15_min_data = get_trimmed_data(
    btc_usdt_15_min_data,
    NUM_WINDOWS,
    LIMIT_TIME,
    in_sample_size=(24 * 30 * 24 * (60 // 15)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 15)) # 6 months
)
btc_usdt_30_min_data = get_trimmed_data(
    btc_usdt_30_min_data,
    NUM_WINDOWS,
    LIMIT_TIME,
    in_sample_size=(24 * 30 * 24 * (60 // 30)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 30)) # 6 months
)

In [1]:
# fig = go.Figure(
#     go.Scatter(
#         y=btc_usdt_30_min_data['close_price'].iloc[::10],
#         x=btc_usdt_30_min_data['close_time'].iloc[::10], 
#         # marker=dict(color='rgb(80, 80, 80)')
#         marker=dict(color='slateblue')
#         ))

# fig.update_layout(
#     yaxis_title="BTC/USDT",
#     xaxis_title="Date",
#         font=dict(
#         # family="Courier New, monospace",
#         size=14,
#     ),
#     autosize=False,
#     width=1200,
#     height=400,
#     margin=dict(l=20, r=20, t=20, b=20),
#     plot_bgcolor='white'
#     )

# fig.update_xaxes(
#     mirror=True,
#     ticks='outside',
#     showline=True,
#     linecolor='black',
#     gridcolor='lightgrey'
# )
# fig.update_yaxes(
#     mirror=True,
#     ticks='outside',
#     showline=True,
#     linecolor='black',
#     gridcolor='lightgrey'
# )

# fig.show()

In [7]:
table_datasets = Texttable()
table_datasets.set_deco(Texttable.HEADER)
table_datasets.set_cols_align(["l", "c", "c", "c"])
table_datasets.set_precision(7)
table_datasets.header([
    "\\textbf{Statistic}",
    "\\makecell{\\textbf{BTC/USDT} \\\\ \\textbf{5min}}",
    "\\makecell{\\textbf{BTC/USDT} \\\\ \\textbf{5min}}",
    "\\makecell{\\textbf{BTC/USDT} \\\\ \\textbf{5min}}",
])
table_datasets.add_row(["count", len(btc_usdt_5_min_data), len(btc_usdt_15_min_data), len(btc_usdt_30_min_data)])
# table_datasets.set_cols_dtype(['t', 'e', 'e', 'e'])
table_datasets.add_row([
    "mean",
    np.mean(btc_usdt_5_min_data['returns']),
    np.mean(btc_usdt_15_min_data['returns']),
    np.mean(btc_usdt_30_min_data['returns']),
])
table_datasets.add_row([
    "std",
    np.std(btc_usdt_5_min_data['returns']),
    np.std(btc_usdt_15_min_data['returns']),
    np.std(btc_usdt_30_min_data['returns']),
])
table_datasets.add_row([
    "min",
    np.min(btc_usdt_5_min_data['returns']),
    np.min(btc_usdt_15_min_data['returns']),
    np.min(btc_usdt_30_min_data['returns']),
])
table_datasets.add_row([
    "25\\% percentile",
    np.percentile(btc_usdt_5_min_data['returns'], 25),
    np.percentile(btc_usdt_15_min_data['returns'], 25),
    np.percentile(btc_usdt_30_min_data['returns'], 25),
])
table_datasets.add_row([
    "50\\% percentile",
    np.percentile(btc_usdt_5_min_data['returns'], 50),
    np.percentile(btc_usdt_15_min_data['returns'], 50),
    np.percentile(btc_usdt_30_min_data['returns'], 50),
])
table_datasets.add_row([
    "75\\% percentile",
    np.percentile(btc_usdt_5_min_data['returns'], 75),
    np.percentile(btc_usdt_15_min_data['returns'], 75),
    np.percentile(btc_usdt_30_min_data['returns'], 75),
])
table_datasets.add_row([
    "max",
    np.max(btc_usdt_5_min_data['returns']),
    np.max(btc_usdt_15_min_data['returns']),
    np.max(btc_usdt_30_min_data['returns']),
])
# table_datasets.set_cols_dtype(['a', 'a', 'a', 'a'])
table_datasets.set_precision(2)
table_datasets.add_row([
    "kurtosis",
    scipy.stats.kurtosis(btc_usdt_5_min_data['returns']),
    scipy.stats.kurtosis(btc_usdt_15_min_data['returns']),
    scipy.stats.kurtosis(btc_usdt_30_min_data['returns']),
])
table_datasets.add_row([
    "skewness",
    scipy.stats.skew(btc_usdt_5_min_data['returns']),
    scipy.stats.skew(btc_usdt_15_min_data['returns']),
    scipy.stats.skew(btc_usdt_30_min_data['returns']),
])
# table_datasets.set_precision(5)
kstest_5min = scipy.stats.kstest(btc_usdt_5_min_data['returns'].to_numpy(), scipy.stats.norm.cdf)
kstest_15min = scipy.stats.kstest(btc_usdt_15_min_data['returns'].to_numpy(), scipy.stats.norm.cdf)
kstest_30min = scipy.stats.kstest(btc_usdt_30_min_data['returns'].to_numpy(), scipy.stats.norm.cdf)
table_datasets.add_row([
    "KS test stat.",
    kstest_5min.statistic,
    kstest_15min.statistic,
    kstest_30min.statistic,
])
table_datasets.set_cols_dtype(['a', 'e', 'e', 'e'])
table_datasets.add_row([
    "KS test p-value",
    kstest_5min.pvalue,
    kstest_15min.pvalue,
    kstest_30min.pvalue,
])
# table_datasets._rows
print(latextable.draw_latex(table_datasets))

NameError: name 'Texttable' is not defined

In [8]:
fig = go.Figure(
    go.Scatter(
        y=btc_usdt_30_min_data['fear_greed_index'].iloc[::10],
        x=btc_usdt_30_min_data['close_time'].iloc[::10], 
        # marker=dict(color='rgb(80, 80, 80)')
        marker=dict(color='slateblue')
        ))

fig.update_layout(
    yaxis_title="Fear & Greed Index value",
    xaxis_title="Date",
        font=dict(
        # family="Courier New, monospace",
        size=14,
    ),
    autosize=False,
    width=1200,
    height=400,
    margin=dict(l=20, r=20, t=20, b=20),
    plot_bgcolor='white'
    )

fig.update_xaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)
fig.update_yaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)

fig.show()

/usr/local/anaconda3/envs/plotly/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:107: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [9]:
fig = go.Figure(
    go.Scatter(
        y=btc_usdt_30_min_data['vix_close_price'].iloc[::10],
        x=btc_usdt_30_min_data['close_time'].iloc[::10], 
        # marker=dict(color='rgb(80, 80, 80)')
        marker=dict(color='slateblue')
        ))

fig.update_layout(
    yaxis_title="VIX Index close value",
    xaxis_title="Date",
        font=dict(
        # family="Courier New, monospace",
        size=14,
    ),
    autosize=False,
    width=1200,
    height=400,
    margin=dict(l=20, r=20, t=20, b=20),
    plot_bgcolor='white'
    )

fig.update_xaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)
fig.update_yaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)

fig.show()

In [10]:
fig = go.Figure(
    go.Scatter(
        y=btc_usdt_30_min_data['effective_rates'].iloc[::10],
        x=btc_usdt_30_min_data['close_time'].iloc[::10], 
        # marker=dict(color='rgb(80, 80, 80)')
        marker=dict(color='slateblue')
        ))

fig.update_layout(
    yaxis_title="FED effective rates",
    xaxis_title="Date",
        font=dict(
        # family="Courier New, monospace",
        size=14,
    ),
    autosize=False,
    width=1200,
    height=400,
    margin=dict(l=20, r=20, t=20, b=20),
    plot_bgcolor='white'
    )

fig.update_xaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)
fig.update_yaxes(
    mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    gridcolor='lightgrey'
)

fig.show()

In [2]:
def split_dataset_moving_window(
        data, 
        num_parts,
        in_sample_size,
        out_of_sample_size):
    result = []
    dataset_len = len(data)
    window_size = in_sample_size + out_of_sample_size

    print(f"In sample size: {in_sample_size}")
    print(f"Out of sample size: {out_of_sample_size}")
    
    for i in range(num_parts):
        part_len = dataset_len - i * out_of_sample_size
        in_sample_part = data.iloc[part_len - window_size: part_len - out_of_sample_size].reset_index(drop=True)
        out_of_sample_part = data.iloc[part_len - out_of_sample_size: part_len].reset_index(drop=True)
        result.append((in_sample_part, out_of_sample_part))
    
    # Return windows in time order
    return list(reversed(result))

def plot_moving_windows(data, windows):

    fig = make_subplots(
        rows=NUM_WINDOWS + 1 + 1,
        cols=1,
        row_heights=[0.05] * (NUM_WINDOWS+1) + [1 - 0.05 * (NUM_WINDOWS+1)],
        vertical_spacing=0.01,
        shared_xaxes=True)

    for i, (in_sample, out_sample) in enumerate(windows):
        fig.add_trace(go.Bar(
            y = [1, 1],
            x = [in_sample['close_time'].iloc[0], out_sample['close_time'].iloc[0]],
            marker_color=['lightgrey', 'darkgrey'],
            width = [
            (in_sample['close_time'].iloc[-1] - in_sample['close_time'].iloc[0]).total_seconds()*1000,
            (out_sample['close_time'].iloc[-1] - out_sample['close_time'].iloc[0]).total_seconds()*1000
            ],
            offset=0
        ), row=i+1, col=1)
    
    fig.add_trace(go.Bar(
        y=[1],
        x=[windows[0][1]['close_time'].iloc[0]],
        marker_color=['darkgrey'],
        width= [(windows[-1][1]['close_time'].iloc[-1] - windows[0][1]['close_time'].iloc[0]).total_seconds()*1000],
        offset=0,
    ), row=NUM_WINDOWS+1, col=1)

    fig.add_trace(go.Scatter(
        y=data['close_price'].iloc[::100],
        x=data['close_time'].iloc[::100],
        marker_color='black',
    ), row=NUM_WINDOWS+2, col=1)

    for i, (in_sample, out_sample) in enumerate(windows):
        fig.add_shape(
            go.layout.Shape(type="line",
                            yref="paper",
                            xref="x",
                            x0=out_sample['close_time'].iloc[0],
                            x1=out_sample['close_time'].iloc[0],
                            y0=0,
                            y1=1,
                            line=dict(dash='dash', color='rgb(140,140,140)')))
        # fig.add_vline(x=out_sample['close_time'].iloc[0])
    
    fig.add_shape(
        go.layout.Shape(type="line",
                        yref="paper",
                        xref="x",
                        x0=windows[NUM_WINDOWS-1][1]['close_time'].iloc[-1],
                        x1=windows[NUM_WINDOWS-1][1]['close_time'].iloc[-1],
                        y0=0,
                        y1=1,
                        line=dict(dash='dash', color='rgb(140,140,140)')))

    fig.update_yaxes(showticklabels=False)
    fig.update_yaxes(showticklabels=True, row=NUM_WINDOWS+1+1, col=1)
    fig.update_xaxes(range=[
        windows[0][0]['close_time'].iloc[0],
        windows[-1][-1]['close_time'].iloc[-1]])
    fig.update_layout(
        showlegend=False,
        plot_bgcolor="white",
        width=1200,
        height=500,
        margin=dict(l=20, r=20, t=20, b=20),
    )
    next(fig.select_xaxes(NUM_WINDOWS+1)).update(
    # mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    # gridcolor='lightgrey',
    title_text="Data"
)

    next(fig.select_yaxes(NUM_WINDOWS+1)).update(
    # mirror=True,
    ticks='outside',
    showline=True,
    linecolor='black',
    # gridcolor='lightgrey',
    title_text="BTC/USDT"
)
    for i in range(NUM_WINDOWS):
        fig.add_annotation(
            x = (windows[i][0]['close_time'].iloc[0]).timestamp()*1000,
            y = 1 - (0.056 * (i)),
            # xref="paper",
            align="left",
            yref="paper",
            text=f"W{i+1}        ",
            showarrow=False
        )
    
    # fig.update_yaxes(title_text="Date", row=NUM_WINDOWS+1, col=0)
    
    # # fig['layout'][f'xaxis{NUM_WINDOWS}_title']['title']='Label x-axis 1'
    # # fig['layout']['xaxis2']['title']='Label x-axis 2'
    # # fig['layout']['yaxis']['title']='Label y-axis 1'
    # # fig['layout']['yaxis2']['title']='Label y-axis 2'
    fig.show()

rolling_windows_30m = split_dataset_moving_window(
    btc_usdt_30_min_data,
    NUM_WINDOWS,
    in_sample_size=(24 * 30 * 24 * (60 // 30)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 30)) # 6 months
)
# plot_moving_windows(btc_usdt_30_min_data, rolling_windows_30m)

NameError: name 'btc_usdt_30_min_data' is not defined

In [53]:
rolling_windows_30m[0][1]['close_time'].iloc[0].timestamp()*1000

1632938399999.0

In [12]:
# import plotly.figure_factory as ff
# fig = ff.create_distplot([w['returns'] for w in windows_out_of_sample_30m],
#                          group_labels=['A', 'B', 'C', 'D', 'E', 'F'],
#                          bin_size=.001,
#                          show_hist=False,
#                          show_box=True,
#                          show_rug=False)

# fig = go.Figure()

# for window in reversed(windows_out_of_sample_30m):
#     fig.add_trace(go.Violin(x=window['returns']))

# fig.update_layout(
#     showlegend=False,
#     width=1200,
#     height=1200,
#     margin=dict(l=20, r=20, t=20, b=20),
# )
# fig.show()

In [8]:
rolling_windows_5m = split_dataset_moving_window(
    btc_usdt_5_min_data,
    NUM_WINDOWS,
    in_sample_size=(24 * 30 * 24 * (60 // 5)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 5)) # 6 months
)
rolling_windows_15m = split_dataset_moving_window(
    btc_usdt_15_min_data,
    NUM_WINDOWS,
    in_sample_size=(24 * 30 * 24 * (60 // 15)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 15)) # 6 months
)
rolling_windows_30m = split_dataset_moving_window(
    btc_usdt_30_min_data,
    NUM_WINDOWS,
    in_sample_size=(24 * 30 * 24 * (60 // 30)), # 24 months
    out_of_sample_size=(6 * 30 * 24 * (60 // 30)) # 6 months
)

In sample size: 207360
Out of sample size: 51840
In sample size: 69120
Out of sample size: 17280
In sample size: 34560
Out of sample size: 8640


In [3]:
def w_distances(windows):
    w_dists = np.empty((NUM_WINDOWS, NUM_WINDOWS))
    for a, b in itertools.product(range(6), repeat=2):
        w_dist = scipy.stats.wasserstein_distance(
            windows[a][1]['returns'],
            windows[b][1]['returns'])
        w_dists[a, b] = w_dist

    return w_dists


def plot_window_returns_distributions(*datasets):
    titles = [
        "BTC/USDT returns 5m",
        "BTC/USDT returns 15m",
        "BTC/USDT returns 30m",
    ]
    for dataset, title in zip(datasets, titles):
        fig = make_subplots(
            rows=1,
            cols=2,
            column_widths=[0.4, 0.6],
            # row_heights=[0.05] * NUM_WINDOWS + [1 - 0.05 * NUM_WINDOWS],
            vertical_spacing=0.1)
        names = [f"W{i+1}"for i in range(NUM_WINDOWS)]
        dists = w_distances(dataset).tolist()
        # fig1 = ff.create_annotated_heatmap(dists)
        # for i in range(len(fig1.data)):
            # fig1.data[i].xaxis='x1'
            # fig1.data[i].yaxis='y1'
        # fig1.layout.xaxis1.update({'anchor': 'y1'})
        # fig1.layout.yaxis1.update({'anchor': 'x1'})
        # fig.layout.update(fig1.layout)
        # fig.add_trace(go.Heatmap(
        #     z=dists,
        #     text=dists,
        #     coloraxis='coloraxis',
        #     # text_auto=True,
        #     y=names,
        #     x=names), row=1, col=1)
        # fig.add_trace(fig1.data[0], row=1, col=1)
        fig.add_trace(px.imshow(dists, text_auto='.4f', x=names, y=names).data[0], 1, 1)

        colors = ['lightseagreen', 'orange', 'mediumpurple', 'hotpink', 'lavender', 'olive']
        for (_, out_of_sample), name, color in zip(dataset, names, colors):
            fig.add_trace(go.Violin(
                x=out_of_sample['returns'],
                name=name,
                # fillcolor=color,
                # line_color=color                
                ), row=1, col=2)

        fig.update_layout(
            xaxis2_range=[-0.1, 0.1],
            showlegend=False,
            width=1000,
            height=400,
            plot_bgcolor="white",
            margin=dict(l=20, r=20, t=50, b=20),
            coloraxis_showscale=False,
            title={
                'text': title,
                'y':0.95,
                'x':0.5,
                'xanchor': 'center',
                'yanchor': 'top',
                'font': {'size': 18}}
            )
        fig.update_coloraxes(
            cmin=0,
            cmax=0.0025,
            # colorscale='gray'
        )
        fig.show()

# plot_window_returns_distributions(rolling_windows_5m, rolling_windows_15m, rolling_windows_30m)

In [23]:
import os
def get_data_windows(project, dataset_name, min_window=0, max_window=5):
    artifact_name = f"{project}/{dataset_name}"
    artifact = wandb.Api().artifact(artifact_name)
    base_path = artifact.download()
    name = artifact.metadata['name']

    result = []
    for i in range(min_window, max_window+1):
        in_sample_name =\
            f"in-sample-{i}"
        in_sample_data = pd.read_csv(os.path.join(
            base_path, name + '-' + in_sample_name + '.csv'))
        out_of_sample_name =\
            f"out-of-sample-{i}"
        out_of_sample_data = pd.read_csv(os.path.join(
            base_path, name + '-' + out_of_sample_name + '.csv'))
        result.append((in_sample_data, out_of_sample_data))

    return result

data_windows_5min = get_data_windows(
    'wne-masters-thesis-testing',
    'btc-usdt-5m:latest',
    min_window=0, 
    max_window=5
)
data_windows_15min = get_data_windows(
    'wne-masters-thesis-testing',
    'btc-usdt-15m:latest',
    min_window=0, 
    max_window=5
)
data_windows_30min = get_data_windows(
    'wne-masters-thesis-testing',
    'btc-usdt-30m:latest',
    min_window=0, 
    max_window=5
)

wandb: Downloading large artifact btc-usdt-5m:latest, 745.12MB. 12 files... 
wandb:   12 of 12 files downloaded.  
Done. 0:0:0.6
wandb: Downloading large artifact btc-usdt-15m:latest, 248.65MB. 12 files... 
wandb:   12 of 12 files downloaded.  
Done. 0:0:0.6
wandb: Downloading large artifact btc-usdt-30m:latest, 124.19MB. 12 files... 
wandb:   12 of 12 files downloaded.  
Done. 0:0:0.4


In [31]:
def data_windows_stats(windows):
    table_datasets = Texttable()
    table_datasets.set_deco(Texttable.HEADER)
    table_datasets.set_cols_align(["l", "c", "c", "c", "c", "c", "c"])
    table_datasets.set_precision(7)
    table_datasets.header([
        "\\textbf{Statistic}",
        "\\makecell{\\textbf{W1}",
        "\\makecell{\\textbf{W2}",
        "\\makecell{\\textbf{W3}",
        "\\makecell{\\textbf{W4}",
        "\\makecell{\\textbf{W5}",
        "\\makecell{\\textbf{W6}",
    ])
    table_datasets.add_row(["count"] + [len(w) for _, w in windows ])
    # table_datasets.set_cols_dtype(['t', 'e', 'e', 'e'])
    table_datasets.add_row(["mean"] + [np.mean(w['returns']) for _, w in windows])
    table_datasets.add_row(["std"] + [np.std(w['returns']) for _, w in windows])
    table_datasets.add_row(["min"] + [np.min(w['returns']) for _, w in windows])
    table_datasets.add_row(["25\\% percentile"] + [np.percentile(w['returns'], 25) for _, w in windows])
    table_datasets.add_row(["50\\% percentile"] + [np.percentile(w['returns'], 50) for _, w in windows])
    table_datasets.add_row(["75\\% percentile"] + [np.percentile(w['returns'], 75) for _, w in windows])
    table_datasets.add_row(["max"] + [np.max(w['returns']) for _, w in windows])

    table_datasets.set_precision(2)
    table_datasets.add_row(["kurtosis"] + [scipy.stats.kurtosis(w['returns']) for _, w in windows])
    table_datasets.add_row(["skewness"] + [scipy.stats.skew(w['returns']) for _, w in windows]),

    ktests = [scipy.stats.kstest(w['returns'], scipy.stats.norm.cdf) for _, w in windows]
    table_datasets.add_row(["KS test stat."] + [k.statistic for k in ktests])
    table_datasets.set_cols_dtype(['a', 'e', 'e', 'e', 'e', 'e', 'e'])
    table_datasets.add_row(["KS test p-value"] + [k.pvalue for k in ktests])
    # table_datasets._rows
    print(latextable.draw_latex(table_datasets))

data_windows_stats(data_windows_5min)
data_windows_stats(data_windows_15min)
data_windows_stats(data_windows_30min)

\begin{table}
	\begin{center}
		\begin{tabular}{lcccccc}
			\textbf{Statistic} & \makecell{\textbf{W1} & \makecell{\textbf{W2} & \makecell{\textbf{W3} & \makecell{\textbf{W4} & \makecell{\textbf{W5} & \makecell{\textbf{W6} \\
			\hline
			count & 51840 & 51840 & 51840 & 51840 & 51840 & 51840 \\
			mean & 0.0000010 & -0.0000089 & 0.0000016 & 0.0000050 & 0.0000080 & 0.0000099 \\
			std & 0.0021663 & 0.0023011 & 0.0015967 & 0.0013956 & 0.0013791 & 0.0016259 \\
			min & -0.0989054 & -0.0438821 & -0.0469833 & -0.0263642 & -0.0866874 & -0.0370693 \\
			25\% percentile & -0.0010410 & -0.0009298 & -0.0005471 & -0.0005338 & -0.0004952 & -0.0006930 \\
			50\% percentile & -0.0000139 & -0.0000029 & 0.0000070 & 0 & 0 & 0.0000064 \\
			75\% percentile & 0.0010127 & 0.0009137 & 0.0005638 & 0.0005350 & 0.0005185 & 0.0007262 \\
			max & 0.0643117 & 0.0426144 & 0.0487321 & 0.0200162 & 0.0501479 & 0.0189663 \\
			kurtosis & 124.60 & 27.33 & 72.17 & 27.74 & 419.46 & 18.82 \\
			skewness & -1.41 & 0.61 & 